In [1]:
import sys  
#sys.executable} -m pip install pandas
import pandas as pd
import numpy as np

#!{sys.executable} -m pip install geopandas
import geopandas as gpd

import requests

import warnings
warnings.filterwarnings('ignore')

#!{sys.executable} -m pip install seaborn
import seaborn as sns
import matplotlib.pyplot as plt

#!{sys.executable} -m pip install folium
import folium
#!{sys.executable} -m pip install geopy

import geopy.distance


In [2]:
# loading data prepared in step 1
df=pd.read_csv('processed_data/selected_states_bg_data.csv')

In [3]:
df.shape

(98298, 45)

In [4]:
df.head()

GISJOIN       STATE  STATEA          COUNTY  COUNTYA  TRACTA  \
0  G06000104001001  California       6  Alameda County        1  400100   
1  G06000104001002  California       6  Alameda County        1  400100   
2  G06000104002001  California       6  Alameda County        1  400200   
3  G06000104002002  California       6  Alameda County        1  400200   
4  G06000104003001  California       6  Alameda County        1  400300   

   BLCK_GRPA  travel_time_<30mins  travel_time_30_to_60_mins  \
0          1                  359                        231   
1          2                  284                        148   
2          1                  138                        238   
3          2                  214                        191   
4          1                  254                        411   

   travel_time_>60_mins  ...  BLKGRPCE        GEOID       NAMELSAD  MTFCC  \
0                    92  ...         1  60014001001  Block Group 1  G5030   
1                    71  ...         2  60014001002  Block Group 2  G5030   
2                    24  ...         1  60014002001  Block Group 1  G5030   
3                    73  ...         2  60014002002  Block Group 2  G5030   
4                    22  ...         1  60014003001  Block Group 1  G5030   

   FUNCSTAT    ALAND  AWATER   INTPTLAT    INTPTLON  \
0         S  5737663       0  37.869878 -122.233621   
1         S  1208194       0  37.857105 -122.223622   
2         S   288070       0  37.849745 -122.248848   
3         S   298490       0  37.846587 -122.250310   
4         S   265695       0  37.843985 -122.248667   

                                            geometry  
0  POLYGON ((-122.24691 37.885355, -122.246645 37...  
1  POLYGON ((-122.234279 37.853626, -122.234094 3...  
2  POLYGON ((-122.255084 37.846069, -122.254239 3...  
3  POLYGON ((-122.257923 37.842605999999996, -122...  
4  POLYGON ((-122.251857 37.844746, -122.251781 3...  

[5 rows x 45 columns]

In [5]:
df.columns

Index(['GISJOIN', 'STATE', 'STATEA', 'COUNTY', 'COUNTYA', 'TRACTA',
       'BLCK_GRPA', 'travel_time_<30mins', 'travel_time_30_to_60_mins',
       'travel_time_>60_mins', 'income_group_<$10k',
       'income_group_$10k_to_$25k', 'income_group_$25k_to_$50k',
       'income_group_$50k_to_$100k', 'income_group_$100k_to_$200k',
       'income_group_>$200k', 'Total_Population', 'Total_Working',
       'Car, truck, or van', 'Taxicab', 'Motorcycle', 'Bicycle', 'Walked',
       'Other means of transport', 'Worked from home', 'In labor force',
       'In labor force: Civilian labor force',
       'In labor force: Civilian labor force: Employed',
       'In labor force: Civilian labor force: Unemployed',
       'In labor force: Armed Forces', 'Not in labor force', 'unique_key',
       'STATEFP', 'COUNTYFP', 'TRACTCE', 'BLKGRPCE', 'GEOID', 'NAMELSAD',
       'MTFCC', 'FUNCSTAT', 'ALAND', 'AWATER', 'INTPTLAT', 'INTPTLON',
       'geometry'],
      dtype='object')

### Dropping unused columns

In [6]:
df.columns[-14:-3]

Index(['unique_key', 'STATEFP', 'COUNTYFP', 'TRACTCE', 'BLKGRPCE', 'GEOID',
       'NAMELSAD', 'MTFCC', 'FUNCSTAT', 'ALAND', 'AWATER'],
      dtype='object')

In [7]:
drop_cols = df.columns[-14:-3].tolist()

In [8]:
df.drop(drop_cols,axis=1,inplace=True)

In [9]:
df.shape

(98298, 34)

In [10]:
df.STATE.unique()

array(['California', 'Connecticut', 'Florida', 'Georgia', 'Mississippi',
       'New Jersey', 'New York', 'Texas', 'Washington'], dtype=object)

### Shorting the points per county

In [11]:
df.COUNTY.nunique()

621

In [12]:
df.STATE.unique()

array(['California', 'Connecticut', 'Florida', 'Georgia', 'Mississippi',
       'New Jersey', 'New York', 'Texas', 'Washington'], dtype=object)

##### Select the state and counties of interest 

#### California

### Texas

In [13]:
state_df=df[df.STATE=='Texas'].reset_index(drop=True)

In [14]:
state_df.shape

(18660, 34)

In [15]:
state_df.COUNTY.nunique()

254

In [16]:
state_df.COUNTY.value_counts().head(10)

Harris County       2830
Dallas County       1570
Tarrant County      1246
Bexar County        1139
Travis County        766
El Paso County       598
Collin County        588
Hidalgo County       572
Denton County        483
Fort Bend County     366
Name: COUNTY, dtype: int64

In [17]:
state_df.groupby(['COUNTY'])['Total_Population'].sum().sort_values(ascending=False).head(100)

COUNTY
Harris County         4680609
Dallas County         2622634
Tarrant County        2077153
Bexar County          1978826
Travis County         1250884
                       ...   
Palo Pinto County       28792
San Jacinto County      28574
Grimes County           28447
Uvalde County           26899
Gillespie County        26668
Name: Total_Population, Length: 100, dtype: int64

In [18]:
np.sum(state_df.Total_Population<1000)

5243

In [19]:
state_df.shape

(18660, 34)

In [20]:
state_df = state_df[state_df.Total_Population>=1000]

In [21]:
# selecting few counties in new york state
#selected_counties = ['Los Angeles County','San Diego County','Riverside County','San Francisco County']
#selected_counties = ['Harris County','Fort Bend County','Montgomery County']

In [22]:
state_df.COUNTY.nunique()

233

In [23]:
# selecting 100 populus counties
selected_counties = state_df.groupby(['COUNTY'])['Total_Population'].sum().sort_values(ascending=False).head(100).index.tolist()

In [24]:
state_selected = state_df[state_df.COUNTY.isin(selected_counties)]
state_selected.COUNTY.value_counts()

Harris County         2187
Dallas County         1295
Tarrant County        1008
Bexar County           882
Travis County          586
                      ... 
Uvalde County           14
Shelby County           14
San Jacinto County      13
Grimes County           13
Gillespie County        13
Name: COUNTY, Length: 100, dtype: int64

In [25]:
state_selected.columns

Index(['GISJOIN', 'STATE', 'STATEA', 'COUNTY', 'COUNTYA', 'TRACTA',
       'BLCK_GRPA', 'travel_time_<30mins', 'travel_time_30_to_60_mins',
       'travel_time_>60_mins', 'income_group_<$10k',
       'income_group_$10k_to_$25k', 'income_group_$25k_to_$50k',
       'income_group_$50k_to_$100k', 'income_group_$100k_to_$200k',
       'income_group_>$200k', 'Total_Population', 'Total_Working',
       'Car, truck, or van', 'Taxicab', 'Motorcycle', 'Bicycle', 'Walked',
       'Other means of transport', 'Worked from home', 'In labor force',
       'In labor force: Civilian labor force',
       'In labor force: Civilian labor force: Employed',
       'In labor force: Civilian labor force: Unemployed',
       'In labor force: Armed Forces', 'Not in labor force', 'INTPTLAT',
       'INTPTLON', 'geometry'],
      dtype='object')

In [26]:
def shortListCordinates(cords,min_distance=2):

    main_list = []
    tp_list=[]
    base_point=cords[0][1:]#[40.7101702, -073.8719151]
    tp_list.append(base_point)

    
    for i,points in enumerate(cords):
        tick=True
        point=points[1:]
        for ip in tp_list:
            if geopy.distance.geodesic(ip, point).km < min_distance:
                tick=False
                break
                #print('Too close',i,point)
                #continue
        if tick:
            #if i%10==0:
                #print(' point saved',i,point)
            tp_list.append(point)
            base_point=point
            main_list.append([points[0]]+ [point])

            
    return main_list

In [27]:
state_selected.head()

GISJOIN  STATE  STATEA           COUNTY  COUNTYA  TRACTA  \
0  G48000109501001  Texas      48  Anderson County        1  950100   
1  G48000109501002  Texas      48  Anderson County        1  950100   
2  G48000109501003  Texas      48  Anderson County        1  950100   
3  G48000109504011  Texas      48  Anderson County        1  950401   
4  G48000109504021  Texas      48  Anderson County        1  950402   

   BLCK_GRPA  travel_time_<30mins  travel_time_30_to_60_mins  \
0          1                  364                        235   
1          2                  269                        402   
2          3                  260                        106   
3          1                  125                         11   
4          1                    0                          0   

   travel_time_>60_mins  ...  Worked from home  In labor force  \
0                     4  ...                13             729   
1                    19  ...                49             817   
2                    30  ...                35             464   
3                     0  ...                 0             136   
4                     0  ...                 0               0   

   In labor force: Civilian labor force  \
0                                   729   
1                                   817   
2                                   464   
3                                   136   
4                                     0   

   In labor force: Civilian labor force: Employed  \
0                                             624   
1                                             757   
2                                             464   
3                                             136   
4                                               0   

   In labor force: Civilian labor force: Unemployed  \
0                                               105   
1                                                60   
2                                                 0   
3                                                 0   
4                                                 0   

   In labor force: Armed Forces  Not in labor force   INTPTLAT   INTPTLON  \
0                             0                 589  32.061063 -95.495745   
1                             0                 591  31.953209 -95.493230   
2                             0                 686  31.980096 -95.623097   
3                             0                4616  31.734637 -95.815710   
4                             0                7335  31.800051 -95.913110   

                                            geometry  
0  POLYGON ((-95.528679 32.061275, -95.528633 32....  
1  POLYGON ((-95.58827199999999 31.95877999999999...  
2  POLYGON ((-95.697025 31.975967999999998, -95.6...  
3  POLYGON ((-95.847911 31.757527999999997, -95.8...  
4  POLYGON ((-95.98367499999999 31.788655, -95.98...  

[5 rows x 34 columns]

In [28]:
# selecting points which are at least 2 kms apart
min_distance=2
suburbs_list = state_selected['COUNTY'].value_counts().index.tolist()

data=state_selected.copy()
# creating dict of lists
# key = county name
# value = list of coordinates 
selected_points={}
for i in suburbs_list[:]:
    print(i,end='--> ')
    points = data[data['COUNTY']==i][['GISJOIN','INTPTLAT','INTPTLON']].values.tolist()
    short_listed_points=shortListCordinates(points,min_distance=min_distance)
    print(len(short_listed_points),' points')
    selected_points[i]=short_listed_points

Harris County--> 482  points
Dallas County--> 266  points
Tarrant County--> 258  points
Bexar County--> 230  points
Travis County--> 178  points
Collin County--> 138  points
Denton County--> 150  points
Hidalgo County--> 162  points
El Paso County--> 104  points
Fort Bend County--> 111  points
Montgomery County--> 161  points
Williamson County--> 99  points
Cameron County--> 92  points
Nueces County--> 56  points
Brazoria County--> 89  points
Bell County--> 82  points
Lubbock County--> 61  points
Galveston County--> 69  points
Webb County--> 34  points
McLennan County--> 69  points
Smith County--> 75  points
Jefferson County--> 51  points
Brazos County--> 38  points
Ellis County--> 72  points
Hays County--> 60  points
Johnson County--> 61  points
Midland County--> 29  points
Ector County--> 32  points
Guadalupe County--> 42  points
Randall County--> 30  points
Parker County--> 58  points
Comal County--> 49  points
Gregg County--> 33  points
Taylor County--> 33  points
Grayson County-->

In [29]:
# coverting dict of lists to single dataframe 
df_list = []
for key in selected_points.keys():
    sub_df=pd.DataFrame(selected_points[key]).rename(columns={0:'geoid',1:'cords'})
    sub_df[['lat','lon']] = pd.DataFrame(sub_df.cords.tolist(), index= sub_df.index)
    #print(sub_df.shape)
    #ny_cords=sub_df['cords'].values.tolist()
    sub_df.drop(['cords'],axis=1,inplace=True)
    df_list.append(sub_df)
state_short_list_df=pd.concat(df_list)
state_short_list_df.shape

(4951, 3)

In [30]:
state_short_list_df.head()

geoid        lat        lon
0  G48020102104001  29.789361 -95.366630
1  G48020102106001  29.810468 -95.361451
2  G48020102108001  29.796990 -95.344962
3  G48020102111023  29.788522 -95.324918
4  G48020102113011  29.772598 -95.337320

In [31]:
plot_cords=state_short_list_df[['lat','lon']].values.tolist()

In [32]:
m = folium.Map(location=plot_cords[0])

for point in plot_cords:
    folium.Circle(
        radius=10,
        location=point,
        popup=str(point),#"The Waterfront",
        color="crimson",
        fill=False,).add_to(m)


m

In [54]:
missing_ids=[]

In [55]:
import requests

def getCategory(cat_id,data):
    for d in data:
        #print(d)
        if d['id']==cat_id:
            return d['name']
        
def FSData(categories,lat,long):
    
    master_list = []
    for i,category in enumerate(categories):
        #print(i+1,end=' ')
        url = "https://api.foursquare.com/v3/places/search?ll={},{}&radius=2000&limit=50&categories={}".format(lat, long,category)

        headers = {
            "Accept": "application/json",
            "Authorization": "fsq3RweDPjzlSp91ioQ5AoUin3RDgNg+PDGGqD/vEMZD9ZY="
        }
        try:
            response = requests.get(url, headers=headers)
            response.raise_for_status()
        except Exception as ex:
            print(ex)
            continue
        
        response=response.json()

        try:
            results = response['results']
        except Exception as ex : 
            print('Error for {}'.format(category))
            print(ex)
            continue
        sub_list = []
        for result in results:
            distance = result['distance']
            name = result['name']
            categoryi = getCategory(category,result['categories'])
            sub_list.append(
            {
                'distance':distance,
                'name' : name,
                'category' : categoryi
            }
            )
        master_list.extend(sub_list)
    return master_list  
    


In [41]:
# converting string to floats. -> coordinates
state_short_list_df.lon=state_short_list_df.lon.astype(float)
state_short_list_df.lat=state_short_list_df.lat.astype(float)

In [42]:
# making lists of lats,longs,geoids
lat_list = state_short_list_df['lat'].values.tolist()
long_list = state_short_list_df['lon'].values.tolist()
geo_list = state_short_list_df['geoid'].values.tolist()

### https://github.com/Factual/places/blob/master/categories/utils/Foursquare_to_NAICS_and_SIC.tsv

In [56]:
def getVenues(subset_data,venue_id,debug=False):
    
    lat_list = subset_data['lat'].values.tolist()
    long_list = subset_data['lon'].values.tolist()
    geo_list = subset_data['geoid'].values.tolist()
    main_list = []
    missing_ids=[]
    i=0
    for geoid,lat,long in zip(geo_list,lat_list,long_list):
        i=i+1
        print(f'{i} ',end='')
        try:
            data=FSData(venue_id,lat,long)
            geo_dub_list=[geoid for i in range(len(data))]
            main_list.extend(np.column_stack([np.array(geo_dub_list),np.array(data)]))
            if debug:
                print('-----DEBUG----')
                if i>5:
                    break
        except Exception as ex:
            print(f'Exception at {geo_id}')
            missing_ids.append(geo_id)
            print(ex)
            continue
    main_df = pd.DataFrame(main_list)
    main_df_prop = pd.DataFrame(main_list)[1].apply(pd.Series)#.shape
    main_df = pd.concat([main_df,main_df_prop],axis=1)
    print(main_df.shape)
    main_df = main_df.rename(columns={0:'geoID'}).drop([1],axis=1)
    main_df_count  = main_df.groupby(['geoID','category']).agg({'name':'count'}).unstack(-1).droplevel(0, axis=1).reset_index()
    main_df_distance  = main_df.groupby(['geoID','category']).agg({'distance':'mean'}).unstack(-1).droplevel(0, axis=1) .reset_index()
    main_processed = main_df_count.merge(main_df_distance,on='geoID',suffixes=['_count','_avg_distance'])

    return main_processed

### food_restaurants

In [ ]:
1000 cords

4 categories

4000 queries


In [57]:
# fo
indian_restaurants_ids= [13199]
chinese_restaurant_id =[13099]
#italian_restaurant_id =[13236]
#mexcian_restaurant_id =[13303]



In [ ]:
point

In [ ]:
{
    venueID:fsflkfjkal,
    categories : ['Restaurant','Chinese','bar']
    coords:
    distance :
    
}

In [58]:
r_ids= [13199,13099]

In [59]:
state_short_list_df.shape

(4951, 3)

In [60]:
state_short_list_df

geoid        lat        lon
0   G48020102104001  29.789361 -95.366630
1   G48020102106001  29.810468 -95.361451
2   G48020102108001  29.796990 -95.344962
3   G48020102111023  29.788522 -95.324918
4   G48020102113011  29.772598 -95.337320
..              ...        ...        ...
6   G48017109503024  30.287108 -98.863377
7   G48017109504021  30.245462 -98.823562
8   G48017109504022  30.260506 -98.863138
9   G48017109505001  30.226166 -98.977310
10  G48017109505002  30.180896 -98.903401

[4951 rows x 3 columns]

In [61]:
len_df=state_short_list_df.shape[0]

In [62]:
split=int(len_df/2)

In [63]:
from time import sleep
from datetime import datetime


In [64]:
# getting restuant count and distance per coord
print('Starting batch 1 at ' + datetime.now().strftime("%H:%M:%S") + '\n')

restaurants_1 = getVenues(state_short_list_df.iloc[:split],r_ids)

print('Batch complete at ' + datetime.now().strftime("%H:%M:%S") + '\n\n')
sleep(60*60)
print('Starting batch 2 at ' + datetime.now().strftime("%H:%M:%S") + '\n')
# getting restuant count and distance per coord
restaurants_2 = getVenues(state_short_list_df.iloc[split:],r_ids)

Starting batch 1 at 15:01:25

1 2 3 4 5 6 7 8 9 10 11 12 13 14 15 16 17 18 19 20 21 22 23 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 45 46 47 48 49 50 51 52 53 54 55 56 57 58 59 60 61 62 63 64 65 66 67 68 69 70 71 72 73 74 75 76 77 78 79 80 81 82 83 84 85 86 87 88 89 90 91 92 93 94 95 96 97 98 99 100 101 102 103 104 105 106 107 108 109 110 111 112 113 114 115 116 117 118 119 120 121 122 123 124 125 126 127 128 129 130 131 132 133 134 135 136 137 138 139 140 141 142 143 144 145 146 147 148 149 150 151 152 153 154 155 156 157 158 159 160 161 162 163 164 165 166 167 168 169 170 171 172 173 174 175 176 177 178 179 180 181 182 183 184 185 186 187 188 189 190 191 192 193 194 195 196 197 198 199 200 201 202 203 204 205 206 207 208 209 210 211 212 213 214 215 216 217 218 219 220 221 222 223 224 225 226 227 228 229 230 231 232 233 234 235 236 237 238 239 240 241 242 243 244 245 246 247 248 249 250 251 252 253 254 255 256 257 258 259 260 261 262 263 264 265 266 267 268 269 27

1227 1228 1229 1230 1231 1232 1233 1234 1235 1236 1237 1238 1239 1240 1241 1242 1243 1244 1245 1246 1247 1248 1249 1250 1251 1252 1253 1254 1255 1256 1257 1258 1259 1260 1261 1262 1263 1264 1265 1266 1267 1268 1269 1270 1271 1272 1273 1274 1275 1276 1277 1278 1279 1280 1281 1282 1283 1284 1285 1286 1287 1288 1289 1290 1291 1292 1293 1294 1295 1296 1297 1298 1299 1300 1301 1302 1303 1304 1305 1306 1307 1308 1309 1310 1311 1312 1313 1314 1315 1316 1317 1318 1319 1320 1321 1322 1323 1324 1325 1326 1327 1328 1329 1330 1331 1332 1333 1334 1335 1336 1337 1338 1339 1340 1341 1342 1343 1344 1345 1346 1347 1348 1349 1350 1351 1352 1353 1354 1355 1356 1357 1358 1359 1360 1361 1362 1363 1364 1365 1366 1367 1368 1369 1370 1371 1372 1373 1374 1375 1376 1377 1378 1379 1380 1381 1382 1383 1384 1385 1386 1387 1388 1389 1390 1391 1392 1393 1394 1395 1396 1397 1398 1399 1400 1401 1402 1403 1404 1405 1406 1407 1408 1409 1410 1411 1412 1413 1414 1415 1416 1417 1418 1419 1420 1421 1422 1423 1424 1425 1426 

1 2 3 4 5 6 7 8 9 10 11 12 13 14 15 16 17 18 19 20 21 22 23 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 45 46 47 48 49 50 51 52 53 54 55 56 57 58 59 60 61 62 63 64 65 66 67 68 69 70 71 72 73 74 75 76 77 78 79 80 81 82 83 84 85 86 87 88 89 90 91 92 93 94 95 96 97 98 99 100 101 102 103 104 105 106 107 108 109 110 111 112 113 114 115 116 117 118 119 120 121 122 123 124 125 126 127 128 129 130 131 132 133 134 135 136 137 138 139 140 141 142 143 144 145 146 147 148 149 150 151 152 153 154 155 156 157 158 159 160 161 162 163 164 165 166 167 168 169 170 171 172 173 174 175 176 177 178 179 180 181 182 183 184 185 186 187 188 189 190 191 192 193 194 195 196 197 198 199 200 201 202 203 204 205 206 207 208 209 210 211 212 213 214 215 216 217 218 219 220 221 222 223 224 225 226 227 228 229 230 231 232 233 234 235 236 237 238 239 240 241 242 243 244 245 246 247 248 249 250 251 252 253 254 255 256 257 258 259 260 261 262 263 264 265 266 267 268 269 270 271 272 273 274 275 276 277 

1861 1862 1863 1864 1865 1866 1867 1868 1869 1870 1871 1872 1873 1874 1875 1876 1877 1878 1879 1880 1881 1882 1883 1884 1885 1886 1887 1888 1889 1890 1891 1892 1893 1894 1895 1896 1897 1898 1899 1900 1901 1902 1903 1904 1905 1906 1907 1908 1909 1910 1911 1912 1913 1914 1915 1916 1917 1918 1919 1920 1921 1922 1923 1924 1925 1926 1927 1928 1929 1930 1931 1932 1933 1934 1935 1936 1937 1938 1939 1940 1941 1942 1943 1944 1945 1946 1947 1948 1949 1950 1951 1952 1953 1954 1955 1956 1957 1958 1959 1960 1961 1962 1963 1964 1965 1966 1967 1968 1969 1970 1971 1972 1973 1974 1975 1976 1977 1978 1979 1980 1981 1982 1983 1984 1985 1986 1987 1988 1989 1990 1991 1992 1993 1994 1995 1996 1997 1998 1999 2000 2001 2002 2003 2004 2005 2006 2007 2008 2009 2010 2011 2012 2013 2014 2015 2016 2017 2018 2019 2020 2021 2022 2023 2024 2025 2026 2027 2028 2029 2030 2031 2032 2033 2034 2035 2036 2037 2038 2039 2040 2041 2042 2043 2044 2045 2046 2047 2048 2049 2050 2051 2052 2053 2054 2055 2056 2057 2058 2059 2060 

In [65]:
restaurants_1.shape

(1176, 5)

In [66]:
restaurants_2.shape

(429, 5)

In [67]:
state_short_list_df.shape

(4951, 3)

In [ ]:
# getting trasportion count and distance per coord
print('Starting batch 1 at ' + datetime.now().strftime("%H:%M:%S") + '\n')
transport1 = getVenues(state_short_list_df,[19043],False)
print('Batch complete at ' + datetime.now().strftime("%H:%M:%S") + '\n\n')
sleep(60*60)

In [69]:
transport1.shape

(83, 3)

In [71]:


print('Starting batch 2 at ' + datetime.now().strftime("%H:%M:%S") + '\n')
transport2 = getVenues(state_short_list_df,[19046],False)
print('Batch complete at ' + datetime.now().strftime("%H:%M:%S") + '\n\n')
sleep(60*60)

print('Starting batch 3 at ' + datetime.now().strftime("%H:%M:%S") + '\n')
transport3 = getVenues(state_short_list_df,[19047],False)
print('Batch complete at ' + datetime.now().strftime("%H:%M:%S") + '\n\n')
sleep(60*60)

print('Starting batch 4 at ' + datetime.now().strftime("%H:%M:%S") + '\n')
transport4 = getVenues(state_short_list_df,[19054],False)
print('Batch complete at ' + datetime.now().strftime("%H:%M:%S") + '\n\n')
sleep(60*60)

Starting batch 2 at 20:05:25

1 429 Client Error: Too Many Requests for url: https://api.foursquare.com/v3/places/search?ll=29.7893615,-95.3666295&radius=2000&limit=50&categories=19046
2 429 Client Error: Too Many Requests for url: https://api.foursquare.com/v3/places/search?ll=29.8104679,-95.3614505&radius=2000&limit=50&categories=19046
3 429 Client Error: Too Many Requests for url: https://api.foursquare.com/v3/places/search?ll=29.7969902,-95.3449623&radius=2000&limit=50&categories=19046
4 429 Client Error: Too Many Requests for url: https://api.foursquare.com/v3/places/search?ll=29.7885224,-95.3249183&radius=2000&limit=50&categories=19046
5 429 Client Error: Too Many Requests for url: https://api.foursquare.com/v3/places/search?ll=29.7725983,-95.3373197&radius=2000&limit=50&categories=19046
6 

KeyboardInterrupt: 

In [52]:
business_df=pd.read_csv('business_data_labels.csv')

In [53]:
select_business_ids=business_df[business_df.Select==1]['foursquare_category_id'].values.tolist()

In [56]:
# getting trasportion count and distance per coord

business_parks = getVenues(state_short_list_df,select_business_ids,False)

1 2 3 4 5 6 7 8 9 10 11 12 13 14 15 16 17 18 19 20 21 22 23 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 45 46 47 48 49 50 51 52 53 54 55 56 57 58 59 60 61 62 63 64 65 66 67 68 69 70 71 72 73 74 75 76 77 78 79 80 81 82 83 84 85 86 87 88 89 90 91 92 93 94 95 96 97 98 99 100 101 102 103 104 105 106 107 108 109 110 111 112 113 114 115 116 117 118 119 120 121 122 123 124 125 126 127 128 129 130 131 132 133 134 135 136 137 138 139 140 141 142 143 144 145 146 147 148 149 150 151 152 153 154 155 156 157 158 159 160 161 162 163 164 165 166 167 168 169 170 171 172 173 174 175 176 177 178 179 180 181 182 183 184 185 186 187 188 189 190 191 192 193 194 195 196 197 198 199 200 201 202 203 204 205 206 207 208 209 210 211 212 213 214 215 216 217 218 219 220 221 222 223 224 225 226 227 228 229 230 231 232 233 234 235 236 237 238 239 240 241 242 243 244 245 246 247 248 249 250 251 252 253 254 255 256 257 258 259 260 261 262 263 264 265 266 267 268 269 270 271 272 273 274 275 276 277 

In [57]:
business_parks[business_parks.columns[1:7]]

category  Business Center_count  \
0                           NaN   
1                           NaN   
2                           NaN   
3                           NaN   
4                           NaN   
..                          ...   
455                         NaN   
456                         NaN   
457                         NaN   
458                         NaN   
459                         NaN   

category  Business and Strategy Consulting Office_count  \
0                                                   4.0   
1                                                   3.0   
2                                                   3.0   
3                                                   1.0   
4                                                   3.0   
..                                                  ...   
455                                                 4.0   
456                                                 NaN   
457                                                 2.0   
458                                                 NaN   
459                                                 NaN   

category  Coworking Space_count  Employment Agency_count  \
0                           1.0                      5.0   
1                           NaN                      1.0   
2                           NaN                      2.0   
3                           NaN                      2.0   
4                           NaN                      NaN   
..                          ...                      ...   
455                         NaN                      NaN   
456                         NaN                      NaN   
457                         NaN                      NaN   
458                         NaN                      NaN   
459                         NaN                      NaN   

category  Office Building_count  Technology Business_count  
0                           4.0                        5.0  
1                           3.0                        NaN  
2                           1.0                        NaN  
3                           3.0                        NaN  
4                           5.0                        NaN  
..                          ...                        ...  
455                         NaN                        1.0  
456                         NaN                        2.0  
457                         NaN                        3.0  
458                         NaN                        1.0  
459                         NaN                        1.0  

[460 rows x 6 columns]

In [58]:
# adding all business venues into one single column
business_parks['Business_Parks_Count'] = business_parks[business_parks.columns[1:7]].sum(axis=1)

In [59]:
print(business_parks.columns)
rm_cols=['Business Center_count',
       'Business and Strategy Consulting Office_count',
       'Coworking Space_count', 'Employment Agency_count',
       'Office Building_count', 'Technology Business_count',
       'Business Center_avg_distance',
       'Business and Strategy Consulting Office_avg_distance',
       'Coworking Space_avg_distance', 'Employment Agency_avg_distance',
       'Office Building_avg_distance', 'Technology Business_avg_distance']

Index(['geoID', 'Business Center_count',
       'Business and Strategy Consulting Office_count',
       'Coworking Space_count', 'Employment Agency_count',
       'Office Building_count', 'Technology Business_count',
       'Business Center_avg_distance',
       'Business and Strategy Consulting Office_avg_distance',
       'Coworking Space_avg_distance', 'Employment Agency_avg_distance',
       'Office Building_avg_distance', 'Technology Business_avg_distance',
       'Business_Parks_Count'],
      dtype='object', name='category')


In [60]:
# removing the columns which are not required
business_parks.drop(rm_cols,axis=1,inplace=True)

In [61]:
business_parks.head()

category            geoID  Business_Parks_Count
0         G48020102104001                  19.0
1         G48020102106001                   7.0
2         G48020102108001                   6.0
3         G48020102111021                   6.0
4         G48020102112001                   8.0

In [62]:
restaurants

category            geoID  Chinese Restaurant_count  Indian Restaurant_count  \
0         G48020102104001                       2.0                      NaN   
1         G48020102106001                       3.0                      NaN   
2         G48020102108001                       NaN                      NaN   
3         G48020102111021                       NaN                      NaN   
4         G48020102112001                       1.0                      1.0   
..                    ...                       ...                      ...   
407       G48020105555042                       NaN                      NaN   
408       G48020105557011                       2.0                      NaN   
409       G48020105557034                       2.0                      NaN   
410       G48020105560001                       NaN                      NaN   
411       G48020105560003                       NaN                      NaN   

category  Italian Restaurant_count  Mexican Restaurant_count  \
0                              2.0                      25.0   
1                              2.0                      16.0   
2                              1.0                      13.0   
3                              NaN                       4.0   
4                              NaN                       1.0   
..                             ...                       ...   
407                            1.0                       1.0   
408                            4.0                       NaN   
409                            3.0                       3.0   
410                            NaN                       1.0   
411                            NaN                       1.0   

category  Chinese Restaurant_avg_distance  Indian Restaurant_avg_distance  \
0                             1321.500000                             NaN   
1                             1524.666667                             NaN   
2                                     NaN                             NaN   
3                                     NaN                             NaN   
4                              888.000000                          1226.0   
..                                    ...                             ...   
407                                   NaN                             NaN   
408                           1008.500000                             NaN   
409                           1568.500000                             NaN   
410                                   NaN                             NaN   
411                                   NaN                             NaN   

category  Italian Restaurant_avg_distance  Mexican Restaurant_avg_distance  
0                              866.500000                      1254.880000  
1                             1765.500000                      1562.687500  
2                             1436.000000                      1535.615385  
3                                     NaN                      1781.500000  
4                                     NaN                       463.000000  
..                                    ...                              ...  
407                           1119.000000                       796.000000  
408                           1371.250000                              NaN  
409                           1508.333333                       787.666667  
410                                   NaN                      1636.000000  
411                                   NaN                       755.000000  

[412 rows x 9 columns]

In [63]:
state_short_list_df.rename(columns={'geoid':'geoID'},inplace=True)

In [65]:
short_list_df=state_short_list_df.copy()

In [66]:
# merging fs data with main data
m1=short_list_df.merge(restaurants,on='geoID',how='left')
m2=m1.merge(transport,on='geoID',how='left')
m3=m2.merge(business_parks,on='geoID',how='left')

In [68]:
#m3.to_csv('processed_data/selected_nj_bg_data_final.csv',index=False)

In [69]:
short_list_df.head()

geoID        lat        lon
0  G48020102104001  29.789361 -95.366630
1  G48020102106001  29.810468 -95.361451
2  G48020102108001  29.796990 -95.344962
3  G48020102111021  29.782645 -95.331337
4  G48020102112001  29.803088 -95.320574

In [70]:
m3.shape

(507, 20)

In [71]:
short_list_df.shape

(507, 3)

In [72]:
m3.rename(columns={'geoID':'GISJOIN'},inplace=True)

In [73]:
df_final=state_selected.merge(m3,on='GISJOIN',how='inner')

In [74]:
df_final.shape

(507, 53)

In [75]:
df_final.head()

GISJOIN  STATE  STATEA         COUNTY  COUNTYA  TRACTA  BLCK_GRPA  \
0  G48020102104001  Texas      48  Harris County      201  210400          1   
1  G48020102106001  Texas      48  Harris County      201  210600          1   
2  G48020102108001  Texas      48  Harris County      201  210800          1   
3  G48020102111021  Texas      48  Harris County      201  211102          1   
4  G48020102112001  Texas      48  Harris County      201  211200          1   

   travel_time_<30mins  travel_time_30_to_60_mins  travel_time_>60_mins  ...  \
0                  740                        249                    60  ...   
1                  350                        247                    65  ...   
2                  176                        162                    31  ...   
3                   30                         41                     0  ...   
4                  246                         92                    92  ...   

   Mexican Restaurant_avg_distance  Bus Stop_count  Metro Station_count  \
0                      1254.880000             NaN                  NaN   
1                      1562.687500             NaN                  NaN   
2                      1535.615385             NaN                  NaN   
3                      1781.500000             NaN                  NaN   
4                       463.000000             NaN                  NaN   

   Public Transportation_count  Rail Station_count  Bus Stop_avg_distance  \
0                          2.0                 3.0                    NaN   
1                          NaN                 3.0                    NaN   
2                          NaN                 NaN                    NaN   
3                          NaN                 1.0                    NaN   
4                          1.0                 NaN                    NaN   

   Metro Station_avg_distance  Public Transportation_avg_distance  \
0                         NaN                              1133.0   
1                         NaN                                 NaN   
2                         NaN                                 NaN   
3                         NaN                                 NaN   
4                         NaN                              1524.0   

   Rail Station_avg_distance  Business_Parks_Count  
0                 807.666667                  19.0  
1                1201.666667                   7.0  
2                        NaN                   6.0  
3                1888.000000                   6.0  
4                        NaN                   8.0  

[5 rows x 53 columns]

In [76]:
df_final.COUNTY.unique()

array(['Harris County'], dtype=object)

In [77]:
df_final.to_csv('processed_data/selected_HUSTON_bg_data_final.csv',index=False)
#m3.to_csv('processed_data/selected_nj_bg_data_final.csv',index=False)